In [46]:
from itertools import chain
import nltk
from sklearn.metrics import classification_report, confusion_matrix
from sklearn.preprocessing import LabelBinarizer
import sklearn
import pycrfsuite
subsample_list = []
from nltk.tokenize import word_tokenize
nltk.download('punkt')
print(sklearn.__version__)

0.23.2


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


This address identification is using conditional random field (CRF) to gauge which could be the Point of interest and street . 


# Explore data step by step and get the results 

In [86]:
import pandas as pd
df_address_train = pd.read_csv('train.csv')
df_address_test = pd.read_csv('test.csv')

In [87]:
sample = df_address_train

In [88]:
subsample = sample

In [89]:
subsample

id                                        raw_address  \
0            0  jl kapuk timur delta sili iii lippo cika 11 a ...   
1            1                                 aye, jati sampurna   
2            2               setu siung 119 rt 5 1 13880 cipayung   
3            3                               toko dita, kertosono   
4            4                                      jl. orde baru   
...        ...                                                ...   
299995  299995               jend ahmad yani 331 kertasari ciamis   
299996  299996                 raya cila kko, cilandak timur kel.   
299997  299997                     tanjung gusta jl. yaya 2 no 17   
299998  299998  jalan cipadu jaya taman asri gang bijaksana 3 ...   
299999  299999          jaya maspion permata blok beryl b2  no.58   

                                       POI/street  
0       /jl kapuk timur delta sili iii lippo cika  
1                                               /  
2                                          /siung  
3                                      toko dita/  
4                                  /jl. orde baru  
...                                           ...  
299995                           /jend ahmad yani  
299996                             /raya cila kko  
299997                                          /  
299998                                taman asri/  
299999                      jaya maspion permata/  

[300000 rows x 3 columns]

In [90]:
subsample['street'] = subsample['POI/street'].apply(lambda x:x.split('/')[1])
subsample['POI'] = subsample['POI/street'].apply(lambda x:x.split('/')[0])

In [91]:
subsample

id                                        raw_address  \
0            0  jl kapuk timur delta sili iii lippo cika 11 a ...   
1            1                                 aye, jati sampurna   
2            2               setu siung 119 rt 5 1 13880 cipayung   
3            3                               toko dita, kertosono   
4            4                                      jl. orde baru   
...        ...                                                ...   
299995  299995               jend ahmad yani 331 kertasari ciamis   
299996  299996                 raya cila kko, cilandak timur kel.   
299997  299997                     tanjung gusta jl. yaya 2 no 17   
299998  299998  jalan cipadu jaya taman asri gang bijaksana 3 ...   
299999  299999          jaya maspion permata blok beryl b2  no.58   

                                       POI/street  \
0       /jl kapuk timur delta sili iii lippo cika   
1                                               /   
2                                          /siung   
3                                      toko dita/   
4                                  /jl. orde baru   
...                                           ...   
299995                           /jend ahmad yani   
299996                             /raya cila kko   
299997                                          /   
299998                                taman asri/   
299999                      jaya maspion permata/   

                                          street                   POI  
0       jl kapuk timur delta sili iii lippo cika                        
1                                                                       
2                                          siung                        
3                                                            toko dita  
4                                  jl. orde baru                        
...                                          ...                   ...  
299995                           jend ahmad yani                        
299996                             raya cila kko                        
299997                                                                  
299998                                                      taman asri  
299999                                            jaya maspion permata  

[300000 rows x 5 columns]

In [18]:
def find_first_index(ra_split, st_split):
    
    if len(st_split) <= len(ra_split): # new
    
        num_iter = len(ra_split) - len(st_split) + 1
        overlap_list = []

        for i in range(num_iter):
            window = ra_split[i: i+len(st_split)]
            overlap = list(set(window) & set(st_split))
            overlap_list.append(len(overlap))

        max_overlap = [e for e in range(len(overlap_list)) if overlap_list[e] == max(overlap_list)]
        if len(max_overlap) == 1:
            return max_overlap[0]

        else:
            count_list = []
            for idx in max_overlap:
                subset_ra = ra_split[idx: idx+len(st_split)]
                count = 0
                for e in range(len(subset_ra)):
                    if subset_ra[e] not in st_split[e]:
                        count += 0
                    else:
                        count += 1
                count_list.append(count)
            index = count_list.index(max(count_list))
            return max_overlap[index]
    else:
        return 0

In [19]:
def fix_street_errors(row):
    
    raw_add = row['raw_address']

    # If a street name is extracted...
    if row['street'] != "":

        raw_add_split = word_tokenize(raw_add)
        
        extr_street = row['street']
        extr_street_split = word_tokenize(extr_street)
        
        # If the extracted street is in the raw address as an entire string, good!
        if extr_street in raw_add:
            return raw_add
        
        # This is where there are discrepancies!
        else:
            index_in_ra = find_first_index(raw_add_split, extr_street_split)
            raw_add_split[index_in_ra: index_in_ra+len(extr_street_split)] = extr_street_split
            updated_raw_add = ' '.join(raw_add_split).replace(' ,', ',').replace(' .', '.').replace(' )', ')').replace(' (', '(').replace(' ?', '?')          
            return updated_raw_add
      
    # If a street name is originally an empty string, we just assume there's no error. 
    else:
        return raw_add

In [20]:
%%time


subsample['cleaned_raw_add'] = subsample.apply(fix_street_errors, axis=1)


# Sanity checks
subsample.loc[[69, 86, 117, 130, 135, 169], :]

Wall time: 37.6 s


id                                        raw_address  \
69    69                     cak 11 nagasari karawang barat   
86    86      simpang tiga kah nasu no 112 28284 bukit raya   
117  117                          ahmad dah iv kukusan beji   
130  130          mangla rege no h1 3 cimekar kel. cileunyi   
135  135  cipinang besar selatan lintas ibadah, cipi jay...   
169  169   taman mer, 13 electr laun system, 2 meruya utara   

                                 POI/street            street  \
69                                  /cakrad            cakrad   
86                             /kaharu nasu       kaharu nasu   
117                        /ahmad dahlan iv   ahmad dahlan iv   
130                        /manglayang rege   manglayang rege   
135          lintas ibadah/cipinang jaya 1a  cipinang jaya 1a   
169  electrolux laundry system/taman meruya      taman meruya   

                           POI  \
69                               
86                               
117                              
130                              
135              lintas ibadah   
169  electrolux laundry system   

                                       cleaned_raw_add  
69                   cakrad 11 nagasari karawang barat  
86    simpang tiga kaharu nasu no 112 28284 bukit raya  
117                       ahmad dahlan iv kukusan beji  
130      manglayang rege no h1 3 cimekar kel. cileunyi  
135  cipinang besar selatan lintas ibadah, cipinang...  
169  taman meruya, 13 electr laun system, 2 meruya ...

In [23]:
def get_street_mapping_dict(row):
    
    raw_add = row['raw_address']

    # If a street name is extracted...
    if row['street'] != "":

        raw_add_split = word_tokenize(raw_add)
        
        extr_street = row['street']
        extr_street_split = word_tokenize(extr_street)
        
        # If the extracted street is in the raw address as an entire string, good!
        if extr_street in raw_add:
            return None
        
        # This is where there are discrepancies!
        else:
            index_in_ra = find_first_index(raw_add_split, extr_street_split)
            before = raw_add_split[index_in_ra: index_in_ra+len(extr_street_split)] 
            before = ' '.join(before)
            return before, extr_street
      
    # If a street name is originally an empty string, we just assume there's no error. 
    else:
        return None

In [22]:
%%timeit
subsample['street_mapping'] = subsample.apply(get_street_mapping_dict, axis=1)

# print("Executed in {} minutes.".format(round((time() - start)/60, 3)))

# Sanity checks
subsample.loc[[69, 86, 117, 130, 135, 169], :]

37.4 s ± 137 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [24]:
subsample.loc[[69, 86, 117, 130, 135, 169], :]

id                                        raw_address  \
69    69                     cak 11 nagasari karawang barat   
86    86      simpang tiga kah nasu no 112 28284 bukit raya   
117  117                          ahmad dah iv kukusan beji   
130  130          mangla rege no h1 3 cimekar kel. cileunyi   
135  135  cipinang besar selatan lintas ibadah, cipi jay...   
169  169   taman mer, 13 electr laun system, 2 meruya utara   

                                 POI/street            street  \
69                                  /cakrad            cakrad   
86                             /kaharu nasu       kaharu nasu   
117                        /ahmad dahlan iv   ahmad dahlan iv   
130                        /manglayang rege   manglayang rege   
135          lintas ibadah/cipinang jaya 1a  cipinang jaya 1a   
169  electrolux laundry system/taman meruya      taman meruya   

                           POI  \
69                               
86                               
117                              
130                              
135              lintas ibadah   
169  electrolux laundry system   

                                       cleaned_raw_add  \
69                   cakrad 11 nagasari karawang barat   
86    simpang tiga kaharu nasu no 112 28284 bukit raya   
117                       ahmad dahlan iv kukusan beji   
130      manglayang rege no h1 3 cimekar kel. cileunyi   
135  cipinang besar selatan lintas ibadah, cipinang...   
169  taman meruya, 13 electr laun system, 2 meruya ...   

                       street_mapping  
69                      (cak, cakrad)  
86            (kah nasu, kaharu nasu)  
117   (ahmad dah iv, ahmad dahlan iv)  
130    (mangla rege, manglayang rege)  
135  (cipi jaya 1a, cipinang jaya 1a)  
169         (taman mer, taman meruya)

In [44]:
subsample['raw_address'] = subsample['cleaned_raw_add']

In [46]:
subsample.to_csv('train.csv')

In [25]:
# Create a separate dataframe containing only values in `street_mapping` columns, i.e., rows where changes occurred
df_with_street_mappings = subsample[subsample['street_mapping'].notnull()]

street_mapping_dict = dict()

# Create a mapping dictionary, where key is the truncated word/words and the value is the corresponding correct word/words
for row, col in df_with_street_mappings.iterrows():
    street_mapping_dict[col['street_mapping'][0]] = col['street_mapping'][1]
    
# How many street errors are there altogether?
print("Length of street mapping dictionary:", len(street_mapping_dict))

Length of street mapping dictionary: 10591


In [26]:
def fix_poi_errors(row):
    
    raw_add = row['cleaned_raw_add']

    # If a POI name is extracted...
    if row['POI'] != "":

        raw_add_split = word_tokenize(raw_add)
        
        extr_poi = row['POI']
        extr_poi_split = word_tokenize(extr_poi)
        
        # If the extracted POI is in the raw address as an entire string, good!
        if extr_poi in raw_add:
            return raw_add
        
        # This is where there are discrepancies!
        else:
            index_in_ra = find_first_index(raw_add_split, extr_poi_split)
            raw_add_split[index_in_ra: index_in_ra+len(extr_poi_split)] = extr_poi_split
            updated_raw_add = ' '.join(raw_add_split).replace(' ,', ',').replace(' .', '.').replace(' )', ')').replace(' (', '(').replace(' ?', '?')          
            return updated_raw_add
      
    # If a POI name is originally an empty string, we just assume there's no error. 
    else:
        return raw_add

In [28]:
%%timeit
subsample['cleaned_raw_add_1'] = subsample.apply(fix_poi_errors, axis=1)

# print("Executed in {} minutes.".format(round((time() - start)/60, 3)))

# Sanity checks
subsample.loc[[10, 11, 40, 110, 152, 157, 169], :]

21.6 s ± 83.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [29]:
def get_poi_mapping_dict(row):
    
    raw_add = row['cleaned_raw_add']

    # If a POI name is extracted...
    if row['POI'] != "":

        raw_add_split = word_tokenize(raw_add)
        
        extr_poi = row['POI']
        extr_poi_split = word_tokenize(extr_poi)
        
        # If the extracted POI is in the raw address as an entire string, good!
        if extr_poi in raw_add:
            return None
        
        # This is where there are discrepancies!
        else:
            index_in_ra = find_first_index(raw_add_split, extr_poi_split)
            before = raw_add_split[index_in_ra: index_in_ra+len(extr_poi_split)] 
            before = ' '.join(before)
            return before, extr_poi
      
    # If a POI name is originally an empty string, we just assume there's no error. 
    else:
        return None

In [31]:
%%timeit
subsample['poi_mapping'] = subsample.apply(get_poi_mapping_dict, axis=1)

# print("Executed in {} minutes.".format(round((time() - start)/60, 3)))

# Sanity checks
subsample.loc[[10, 11, 40, 110, 152, 157, 169], :]

21.5 s ± 64.1 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [33]:
df_with_poi_mappings = subsample[subsample['poi_mapping'].notnull()]

poi_mapping_dict = dict()

# Create a mapping dictionary, where key is the truncated word/words and the value is the corresponding correct word/words
for row, col in df_with_poi_mappings.iterrows():
    poi_mapping_dict[col['poi_mapping'][0]] = col['poi_mapping'][1]
    
# How many POI errors are there altogether?
print("Length of POI mapping dictionary:", len(poi_mapping_dict))

Length of POI mapping dictionary: 43382


In [34]:
# Select required columns
cleaned_df = subsample[['id','cleaned_raw_add_1', 'POI', 'street']]

# Rename columns
cleaned_df.columns = ['id', 'raw_address', 'POI', 'street']

# Sanity checks
cleaned_df.loc[[10, 11, 40, 69, 86, 110, 117, 130, 135, 152, 157, 169], :]

id                                        raw_address  \
10    10  cikahuripan sd negeri bojong 02 klap boj, no 5...   
11    11                                yayasan atohariyah,   
40    40        markaz tabligh metro iringmulyo metro timur   
69    69                  cakrad 11 nagasari karawang barat   
86    86   simpang tiga kaharu nasu no 112 28284 bukit raya   
110  110              cv. hingdi oto kencana, sido ii, q 29   
117  117                       ahmad dahlan iv kukusan beji   
130  130      manglayang rege no h1 3 cimekar kel. cileunyi   
135  135  cipinang besar selatan lintas ibadah, cipinang...   
152  152  ujung harapan, no 48a pd. karya warga mandiri ...   
157  157                 alun - alun kuliner nusantara, kar   
169  169  taman meruya, 13 electrolux laundry system, 2 ...   

                               POI            street  
10             sd negeri bojong 02          klap boj  
11              yayasan atohariyah                    
40            markaz tabligh metro                    
69                                            cakrad  
86                                       kaharu nasu  
110         cv. hingdi oto kencana           sido ii  
117                                  ahmad dahlan iv  
130                                  manglayang rege  
135                  lintas ibadah  cipinang jaya 1a  
152   pd. karya warga mandiri cimb     ujung harapan  
157  alun - alun kuliner nusantara               kar  
169      electrolux laundry system      taman meruya

In [36]:
# Load test dataset
test_df = pd.read_csv('test.csv')

# Preview
test_df.head()

id                                    raw_address
0   0          s. par 53 sidanegara 4 cilacap tengah
1   1          angg per, baloi indah kel. lubuk baja
2   2                          asma laun, mand imog,
3   3  ud agung rej, raya nga sri wedari karanganyar
4   4                     cut mutia, 35 baiturrahman

In [37]:
new_street_mapping_dict = {k: v for k, v in street_mapping_dict.items() if len(k.split()) > 1}
new_poi_mapping_dict = {k: v for k, v in poi_mapping_dict.items() if len(k.split()) > 1}

print("Length of street mapping dictionary after removing single words:", len(new_street_mapping_dict))
print("Length of POI mapping dictionary after removing single words:", len(new_poi_mapping_dict))

Length of street mapping dictionary after removing single words: 9111
Length of POI mapping dictionary after removing single words: 41735


In [38]:

# Replace truncated words in raw_address of test set with correct street labels
count1 = 0
for row, col in test_df.iterrows():
    for k, v in new_street_mapping_dict.items():
        if k in col['raw_address']:
            test_df.loc[row, 'raw_address'] = test_df.loc[row, 'raw_address'].replace(k, v)
            count1 += 1
            
print("Number of raw addresses updated due to errors in street labels:", count1)

# Replace truncated words in raw_address of test set with correct POI labels
count2 = 0
for row, col in test_df.iterrows():
    for k, v in new_poi_mapping_dict.items():
        if k in col['raw_address']:
            test_df.loc[row, 'raw_address'] = test_df.loc[row, 'raw_address'].replace(k, v)
            count2 += 1

print("Number of raw addresses updated due to errors in POI labels:", count2)

print("Executed in {} minutes.".format(round((time() - start)/60, 3)))

test_df

Number of raw addresses updated due to errors in street labels: 18913
Number of raw addresses updated due to errors in POI labels: 4553


NameError: name 'time' is not defined

In [32]:
test_df.to_csv('cleaned_raw_address.csv')

NameError: name 'test_df' is not defined

In [23]:
#subsample['raw_address'] = subsample['cleaned_raw_add']

In [92]:
subsample = subsample[subsample['POI/street'] != '/']

In [93]:
subsample_list = []
from nltk.tokenize import word_tokenize
nltk.download('punkt')
for ind,each_sample in subsample.iterrows():
    sublist = []
    for each_word in word_tokenize(each_sample['raw_address']):
        if each_word in each_sample['street']:
            sublist.append((each_word,'NP','street'))
        elif each_word in each_sample['POI']:
            sublist.append((each_word,'NP','POI'))
        else:
            sublist.append((each_word,'NA','O'))
    subsample_list.append(sublist)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [94]:
len(subsample_list)

268007

# Testing data portion

In [106]:
test_dataframe = pd.read_csv('test.csv')

In [107]:
subsample_list = []
from nltk.tokenize import word_tokenize
nltk.download('punkt')
for ind,each_sample in test_dataframe.iterrows():
    sublist = []
    for each_word in word_tokenize(each_sample['raw_address']):
#         if each_word in each_sample['street']:
#             sublist.append((each_word,'NP','street'))
#         elif each_word in each_sample['POI']:
#             sublist.append((each_word,'NP','POI'))
#         else:
        sublist.append((each_word,'NA','O'))
    subsample_list.append(sublist)

[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\User\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


In [108]:
len(subsample_list)

50000

In [116]:
for ind,test_df in test_dataframe.iterrows():
    street_string = ''
    street_indx = []
    street_indx = [i for i, e in enumerate(y_pred[ind]) if e == 'street']
    for num in street_indx:
        print(street_indx)
        print(test_df['raw_address'])
        if word_tokenize(test_df['raw_address'])[num] in [',','.']:
            street_string = street_string+word_tokenize(test_df['raw_address'])[num]
        else:
            street_string = street_string+' '+word_tokenize(test_df['raw_address'])[num]
    
    POI_string = ''
    POI_indx = []
    POI_indx = [i for i, e in enumerate(y_pred[ind]) if e == 'POI']
    for num in POI_indx: 
        if word_tokenize(test_df['raw_address'])[num] in [',','.']:
            POI_string = POI_string+word_tokenize(test_df['raw_address'])[num]
        else:
            POI_string = POI_string+' '+word_tokenize(test_df['raw_address'])[num]
    test_dataframe.at[ind,'street'] = street_string.strip()
    test_dataframe.at[ind,'POI'] = POI_string.strip()

    # find the index of where is street and POI
#     test_dataframe.at[ind,'POI'] = 'abc'

[0, 1]
s. par 53 sidanegara 4 cilacap tengah
[0, 1]
s. par 53 sidanegara 4 cilacap tengah
[0, 1]
angg per, baloi indah kel. lubuk baja
[0, 1]
angg per, baloi indah kel. lubuk baja
[3, 4]
asma laun, mand imog,
[3, 4]
asma laun, mand imog,
[4, 5, 6]
ud agung rej, raya nga sri wedari karanganyar
[4, 5, 6]
ud agung rej, raya nga sri wedari karanganyar
[4, 5, 6]
ud agung rej, raya nga sri wedari karanganyar
[0, 1]
cut mutia, 35 baiturrahman
[0, 1]
cut mutia, 35 baiturrahman
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka jaya sukarami
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka jaya sukarami
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka jaya sukarami
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka jaya sukarami
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka jaya sukarami
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka jaya sukarami
[0, 1, 2, 3, 4, 5, 7]
pem dos dapur ala perum gar no a 12 suka j

[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 15, 16, 18]
jl. kunto jl. krap perm gg. i, no 7 merbung ruko perum krapyak, citra indah
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 15, 16, 18]
jl. kunto jl. krap perm gg. i, no 7 merbung ruko perum krapyak, citra indah
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 15, 16, 18]
jl. kunto jl. krap perm gg. i, no 7 merbung ruko perum krapyak, citra indah
[0, 1, 2, 3, 4, 5, 6, 7, 8, 9, 15, 16, 18]
jl. kunto jl. krap perm gg. i, no 7 merbung ruko perum krapyak, citra indah
[9, 10, 11]
bca finance, kcu bca samarinda lantai 4, jl jendral sudirman no 30, pasar pagi
[9, 10, 11]
bca finance, kcu bca samarinda lantai 4, jl jendral sudirman no 30, pasar pagi
[9, 10, 11]
bca finance, kcu bca samarinda lantai 4, jl jendral sudirman no 30, pasar pagi
[1, 2, 3]
cipamokolan pu asih v no 13 rancasari
[1, 2, 3]
cipamokolan pu asih v no 13 rancasari
[1, 2, 3]
cipamokolan pu asih v no 13 rancasari
[3, 4, 5]
pencucian salju pw jend a yani,
[3, 4, 5]
pencucian salju pw jend a yani,
[3, 4, 5]
pencucian sal

[2]
bandar senembah sawo 5 binjai barat
[0, 1]
fachr raya 6 kampung bali pasar regional tanah abang b 6 tanah abang
[0, 1]
fachr raya 6 kampung bali pasar regional tanah abang b 6 tanah abang
[9, 10, 11]
kantor bpn kabupaten gianyar, komplek civic center, jl. sahadewa no.7, gianyar, bali 80511
[9, 10, 11]
kantor bpn kabupaten gianyar, komplek civic center, jl. sahadewa no.7, gianyar, bali 80511
[9, 10, 11]
kantor bpn kabupaten gianyar, komplek civic center, jl. sahadewa no.7, gianyar, bali 80511
[1, 2, 3, 4]
sampiran jl. hijau raya no 17
[1, 2, 3, 4]
sampiran jl. hijau raya no 17
[1, 2, 3, 4]
sampiran jl. hijau raya no 17
[1, 2, 3, 4]
sampiran jl. hijau raya no 17
[5]
rumah makan duo ser, sos,
[0, 1]
gajah mada, asean elektro
[0, 1]
gajah mada, asean elektro
[1, 2, 3]
nerogtog kh has ash 1 rt 4 8 cipondoh
[1, 2, 3]
nerogtog kh has ash 1 rt 4 8 cipondoh
[1, 2, 3]
nerogtog kh has ash 1 rt 4 8 cipondoh
[0, 1]
aes nasu, 16 ace hardware
[0, 1]
aes nasu, 16 ace hardware
[0]
uday, no 4 badan 

[0]
sawo 41 bitera gianyar
[0, 1]
angg dalam grendeng purwokerto utara
[0, 1]
angg dalam grendeng purwokerto utara
[4]
moena fresh denpasar, padma,
[0, 1]
tang turi simomulyo sukomanunggal
[0, 1]
tang turi simomulyo sukomanunggal
[0]
mer pondok cabe udik pamulang
[0, 1]
pangeran muha, musholla al-ikhwan, sukahaji
[0, 1]
pangeran muha, musholla al-ikhwan, sukahaji
[0, 1]
yos suda wringin agung
[0, 1]
yos suda wringin agung
[4, 5]
jagasatru dapur cokelat, kesa dalam, no 94 pekalipan
[4, 5]
jagasatru dapur cokelat, kesa dalam, no 94 pekalipan
[0]
darm, pahandut pahandut
[0, 1, 2, 3, 4]
jl. boule raya grand kalibaru cilodong
[0, 1, 2, 3, 4]
jl. boule raya grand kalibaru cilodong
[0, 1, 2, 3, 4]
jl. boule raya grand kalibaru cilodong
[0, 1, 2, 3, 4]
jl. boule raya grand kalibaru cilodong
[0, 1, 2, 3, 4]
jl. boule raya grand kalibaru cilodong
[0]
jamba, jambangan kel.
[3, 4, 5, 6]
sarana niaga cargo h o s cokr,
[3, 4, 5, 6]
sarana niaga cargo h o s cokr,
[3, 4, 5, 6]
sarana niaga cargo h o s

[0, 1]
taw mangu, 9 pancaran kasih - lawang, lowokwaru
[0, 1]
taw mangu, 9 pancaran kasih - lawang, lowokwaru
[0, 1]
raya payak, koperasi sutra ketinggian, sarilamak
[0, 1]
raya payak, koperasi sutra ketinggian, sarilamak
[0, 1]
prima x
[0, 1]
prima x
[0, 1, 2]
gg. jat 86 tonja denpasar utara
[0, 1, 2]
gg. jat 86 tonja denpasar utara
[0, 1, 2]
gg. jat 86 tonja denpasar utara
[3, 4, 5, 6, 7]
toko may, jl. k.z. abidin, belakang pondok
[3, 4, 5, 6, 7]
toko may, jl. k.z. abidin, belakang pondok
[3, 4, 5, 6, 7]
toko may, jl. k.z. abidin, belakang pondok
[3, 4, 5, 6, 7]
toko may, jl. k.z. abidin, belakang pondok
[3, 4, 5, 6, 7]
toko may, jl. k.z. abidin, belakang pondok
[0, 1, 2]
t orc bint 75 pondok pucung pondok aren
[0, 1, 2]
t orc bint 75 pondok pucung pondok aren
[0, 1, 2]
t orc bint 75 pondok pucung pondok aren
[1]
sukomanunggal suko 38 1 sukomanunggal
[0, 1]
raya mustik 55 mustikasari rt 3 1 mustika jaya
[0, 1]
raya mustik 55 mustikasari rt 3 1 mustika jaya
[2, 3]
alfamart, trans kal,

...

dok ism, 29 sananwetan sanan wetan
[0, 1]
gg. one coffee, no. 3. bandar jawa kampung jawa (beberapa rumah sebelum one coffee)
[0, 1]
gg. one coffee, no. 3. bandar jawa kampung jawa (beberapa rumah sebelum one coffee)
[3, 4]
sand holiday, alt cibu, no 16 17433
[3, 4]
sand holiday, alt cibu, no 16 17433
[0]
t.ub, cot gapu kota juang
[0]
kasu 64 heledulaa selatan kota timur
[1, 2, 3]
jomblang tand selatan 10 7 candisari
[1, 2, 3]
jomblang tand selatan 10 7 candisari
[1, 2, 3]
jomblang tand selatan 10 7 candisari
[0, 1, 2]
nga jaya sela, 2 pucang sewu manyar
[0, 1, 2]
nga jaya sela, 2 pucang sewu manyar
[0, 1, 2]
nga jaya sela, 2 pucang sewu manyar
[1, 2, 3]
pasirgombong indu pasir gomb 145 rt 1 rw 5 17530 cikarang utara
[1, 2, 3]
pasirgombong indu pasir gomb 145 rt 1 rw 5 17530 cikarang utara
[1, 2, 3]
pasirgombong indu pasir gomb 145 rt 1 rw 5 17530 cikarang utara
[0, 1, 2]
lumbu ten viii no 308 bojong rawalumbu 28
[0, 1, 2]
lumbu ten viii no 308 bojong rawalumbu 28
[0, 1, 2]
lumbu ten v

[1, 2]
salon k u,
[1, 2]
salon k u,
[0, 1, 2, 3]
sul mah bad ii 62 alang alang lebar alang-alang lebar
[0, 1, 2, 3]
sul mah bad ii 62 alang alang lebar alang-alang lebar
[0, 1, 2, 3]
sul mah bad ii 62 alang alang lebar alang-alang lebar
[0, 1, 2, 3]
sul mah bad ii 62 alang alang lebar alang-alang lebar
[0]
pen, 6 sawangan
[0, 1, 2]
podo marem majap, prajurit kulon
[0, 1, 2]
podo marem majap, prajurit kulon
[0, 1, 2]
podo marem majap, prajurit kulon
[5, 6]
nakeysha gor des inte, raya laswi, wargamekar
[5, 6]
nakeysha gor des inte, raya laswi, wargamekar
[0, 1, 2]
keja muti v 415a rt 0 0 60112 mulyorejo
[0, 1, 2]
keja muti v 415a rt 0 0 60112 mulyorejo
[0, 1, 2]
keja muti v 415a rt 0 0 60112 mulyorejo
[0, 1, 2]
joglo joglo raya rt 3 8 kembangan
[0, 1, 2]
joglo joglo raya rt 3 8 kembangan
[0, 1, 2]
joglo joglo raya rt 3 8 kembangan
[0, 1, 2]
jend ahmad yani, no 948 tangga takat seberang ulu ii
[0, 1, 2]
jend ahmad yani, no 948 tangga takat seberang ulu ii
[0, 1, 2]
jend ahmad yani, no 948

[0, 1]
dukuh kup no 46 dah fotocopy, rw 9 pakis sawahan
[0, 1]
dukuh kup no 46 dah fotocopy, rw 9 pakis sawahan
[0, 1]
oti raya 116 cipayung ciputat
[0, 1]
oti raya 116 cipayung ciputat
[0, 1, 2, 3, 4, 5]
pakis dukuh kup timur xii a 21-a rt 2 8 60256
[0, 1, 2, 3, 4, 5]
pakis dukuh kup timur xii a 21-a rt 2 8 60256
[0, 1, 2, 3, 4, 5]
pakis dukuh kup timur xii a 21-a rt 2 8 60256
[0, 1, 2, 3, 4, 5]
pakis dukuh kup timur xii a 21-a rt 2 8 60256
[0, 1, 2, 3, 4, 5]
pakis dukuh kup timur xii a 21-a rt 2 8 60256
[0, 1, 2, 3, 4, 5]
pakis dukuh kup timur xii a 21-a rt 2 8 60256
[3, 4, 5, 6, 7, 8]
kota matsum i jl. sutri gg. amal no 47a medan area
[3, 4, 5, 6, 7, 8]
kota matsum i jl. sutri gg. amal no 47a medan area
[3, 4, 5, 6, 7, 8]
kota matsum i jl. sutri gg. amal no 47a medan area
[3, 4, 5, 6, 7, 8]
kota matsum i jl. sutri gg. amal no 47a medan area
[3, 4, 5, 6, 7, 8]
kota matsum i jl. sutri gg. amal no 47a medan area
[3, 4, 5, 6, 7, 8]
kota matsum i jl. sutri gg. amal no 47a medan area
[3, 

[0, 1, 2, 3]
keja putih tam xxiii 18 kejawaan putih tamba rw 4 mulyorejo
[0, 1, 2, 3]
keja putih tam xxiii 18 kejawaan putih tamba rw 4 mulyorejo
[0, 1, 2, 3]
keja putih tam xxiii 18 kejawaan putih tamba rw 4 mulyorejo
[0, 1, 2, 3]
keja putih tam xxiii 18 kejawaan putih tamba rw 4 mulyorejo
[0, 1]
cipa galung, bungursari
[0, 1]
cipa galung, bungursari
[0, 1]
imog barat sumberagung jetis
[0, 1]
imog barat sumberagung jetis
[1, 2, 3]
yosowilangun tanj wira ii, no 39 61151 manyar
[1, 2, 3]
yosowilangun tanj wira ii, no 39 61151 manyar
[1, 2, 3]
yosowilangun tanj wira ii, no 39 61151 manyar
[0, 1]
jalur 5 173 ketapang mentawa baru (ketapang)
[0, 1]
jalur 5 173 ketapang mentawa baru (ketapang)
[0, 1]
mawar raya, larangan
[0, 1]
mawar raya, larangan
[0, 1]
a man, biangkeke pajukukang
[0, 1]
a man, biangkeke pajukukang
[0, 1, 2, 3]
gg. muhaj ii pekauman banjarmasin selatan
[0, 1, 2, 3]
gg. muhaj ii pekauman banjarmasin selatan
[0, 1, 2, 3]
gg. muhaj ii pekauman banjarmasin selatan
[0, 1, 2, 3

[0, 1, 2]
raya alas keda, 19 banjar anyar kediri
[0, 1, 2]
raya alas keda, 19 banjar anyar kediri
[0, 1, 2]
raya alas keda, 19 banjar anyar kediri
[0]
kal, 6
[0, 1]
pan nipah, no 89 83135 mataram
[0, 1]
pan nipah, no 89 83135 mataram
[0, 1]
raya pesi 24 ketapang kademangan
[0, 1]
raya pesi 24 ketapang kademangan
[4]
depot bu deon, ker,
[0, 1, 2]
tegal rotan raya 18 rt 2 rw 7 15413 ciputat
[0, 1, 2]
tegal rotan raya 18 rt 2 rw 7 15413 ciputat
[0, 1, 2]
tegal rotan raya 18 rt 2 rw 7 15413 ciputat
[0]
nn cihuni pagedangan
[0, 1, 2]
mas raya baraya bontoala
[0, 1, 2]
mas raya baraya bontoala
[0, 1, 2]
mas raya baraya bontoala
[4, 5]
beng bang mista, banj pul
[4, 5]
beng bang mista, banj pul
[0, 1]
raya batu telukambulu batujaya
[0, 1]
raya batu telukambulu batujaya
[3, 4, 5]
x tra cell d. i. panja,
[3, 4, 5]
x tra cell d. i. panja,
[3, 4, 5]
x tra cell d. i. panja,
[0, 1]
a sal ronggomulyo tuban
[0, 1]
a sal ronggomulyo tuban
[0, 1, 2]
kapas baru v 3 gading 7 tambaksari
[0, 1, 2]
kapas bar

In [117]:
test_dataframe['POI/street'] = test_dataframe['POI']+'/'+ test_dataframe['street']

In [118]:
test_dataframe.to_csv('test_resultv6.csv')

# Start running the feature and training

In [95]:
from re import search

def containsymbol(string):
    if search(',|\.|-', string):
        return True
    else:
        return False
    


def issymbol(string):
    if string in [',','.','-']:
        return True
    else:
        return False
    
def isempty(string):
    if string in [',','.','-']:
        return True
    else:
        return False

In [96]:
def word2features(sent, i):
    word = sent[i][0]
    postag = sent[i][1]
    features = [
        'bias',
        'word.lower=' + word.lower(),
        'word[-3:]=' + word[-3:],
        'word[-2:]=' + word[-2:],
        'word.isupper=%s' % word.isupper(),
        'word.istitle=%s' % word.istitle(),
        'word.isdigit=%s' % word.isdigit(),
        'word.issymbol=%s' % issymbol(word),
#         'postag=' + postag,
#         'postag[:2]=' + postag[:2],
    ]
    if i > 0:
        word1 = sent[i-1][0]
        postag1 = sent[i-1][1]
        features.extend([
            '-1:word.lower=' + word1.lower(),
            '-1:word.istitle=%s' % word1.istitle(),
            '-1:word.isupper=%s' % word1.isupper(),
            '-1:word.issymbol=%s' % issymbol(word),
#             '-1:postag=' + postag1,
#             '-1:postag[:2]=' + postag1[:2],
        ])
    else:
        features.append('BOS')
        
    if i < len(sent)-1:
        word1 = sent[i+1][0]
        postag1 = sent[i+1][1]
        features.extend([
            '+1:word.lower=' + word1.lower(),
            '+1:word.istitle=%s' % word1.istitle(),
            '+1:word.isupper=%s' % word1.isupper(),
            '+1:word.issymbol=%s' % issymbol(word),
#             '+1:postag=' + postag1,
#             '+1:postag[:2]=' + postag1[:2],
        ])
    else:
        features.append('EOS')
                
    return features


def sent2features(sent):
    return [word2features(sent, i) for i in range(len(sent))]

def sent2labels(sent):
    return [label for token, postag, label in sent]

def sent2tokens(sent):
    return [token for token, postag, label in sent]    

This is what word2features extracts:

Extract the features from the data:

In [97]:
%%time
# X_train = [sent2features(s) for s in subsample_list[:190000]]
# y_train = [sent2labels(s) for s in subsample_list[:190000]]

# X_test = [sent2features(s) for s in subsample_list[190000:]]
# y_test = [sent2labels(s) for s in subsample_list[190000:]]
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split([sent2features(s) for s in subsample_list], [sent2labels(s) for s in subsample_list], test_size=0.25)

Wall time: 12.6 s


## Train the model

To train the model, we create pycrfsuite.Trainer, load the training data and call 'train' method. 
First, create pycrfsuite.Trainer and load the training data to CRFsuite:

In [98]:
%%time
trainer = pycrfsuite.Trainer(verbose=False)

for xseq, yseq in zip(X_train, y_train):
    trainer.append(xseq, yseq)

Wall time: 15.2 s


In [99]:
len(X_train)

201005

Set training parameters. We will use L-BFGS training algorithm (it is default) with Elastic Net (L1 + L2) regularization.
Lasso for L1 and Ridge for L2

In [100]:
trainer.set_params({
    'c1': 1.0,   # coefficient for L1 penalty
    'c2': 1e-3,  # coefficient for L2 penalty
    'max_iterations': 200,  # stop earlier

    # include transitions that are possible, but not observed
    'feature.possible_transitions': True
})

Possible parameters for the default training algorithm:

Train the model:

In [101]:
%%time
trainer.train('cstreet')

Wall time: 2min 20s


## Make predictions

To use the trained model, create pycrfsuite.Tagger, open the model and use "tag" method:

In [110]:
len(subsample_list)

50000

In [111]:
X_test = [sent2features(s) for s in subsample_list[:]]
y_test = [sent2labels(s) for s in subsample_list[:]]

In [112]:
len(X_test)

50000

In [113]:
tagger = pycrfsuite.Tagger()
tagger.open('cstreet')

Let's tag a sentence to see how it works:

## Evaluate the model

In [103]:
def bio_classification_report(y_true, y_pred):
    """
    Classification report for a list of BIO-encoded sequences.
    It computes token-level metrics and discards "O" labels.
    
    Note that it requires scikit-learn 0.15+ (or a version from github master)
    to calculate averages properly!
    """
    lb = LabelBinarizer()
    y_true_combined = lb.fit_transform(list(chain.from_iterable(y_true)))
    y_pred_combined = lb.transform(list(chain.from_iterable(y_pred)))
        
    tagset = set(lb.classes_) 
    tagset = sorted(tagset, key=lambda tag: tag.split('-', 1)[::-1])
    class_indices = {cls: idx for idx, cls in enumerate(lb.classes_)}
    
    return classification_report(
        y_true_combined,
        y_pred_combined,
        labels = [class_indices[cls] for cls in tagset],
        target_names = tagset,
    )

Predict entity labels for all sentences in our testing set ('testb' Spanish data):

In [114]:
%%time
y_pred = [tagger.tag(xseq) for xseq in X_test]

Wall time: 2.73 s


In [115]:
len(y_pred)

50000

..and check the result. Note this report is not comparable to results in CONLL2002 papers because here we check per-token results (not per-entity). Per-entity numbers will be worse.  

In [49]:
subsample[190000:]['raw_address'].values

array(['kayu putih swad 3 rt 6 9 13210',
       'tualang lingkungan x, jln gg.b perbaungan',
       'toko suka hat kh wahid has,', ...,
       'tanjung gusta jl. yaya 2 no 17',
       'jalan cipadu jaya taman asri gang bijaksana 3 rt02 03 no 57.',
       'jaya maspion permata blok beryl b2  no.58'], dtype=object)

In [65]:
subsample[subsample['POI'].str.contains('kios asmi')]

id          raw_address  POI/street street        POI
299992  299992  kios asmi panaikang  kios asmi/         kios asmi

In [50]:
new_df = pd.DataFrame()
new_df['X_test'] = X_test
new_df['Y_test'] = y_test
new_df['Y_pred'] = y_pred
new_df['raw_address'] = subsample[190000:]['raw_address'].values

In [66]:
new_df.query('Y_test!=Y_pred')[50:100]

X_test  \
119  [[bias, word.lower=willis, word[-3:]=lis, word...   
121  [[bias, word.lower=wonokromo, word[-3:]=omo, w...   
123  [[bias, word.lower=jl, word[-3:]=jl, word[-2:]...   
125  [[bias, word.lower=citarum, word[-3:]=rum, wor...   
126  [[bias, word.lower=mekar, word[-3:]=kar, word[...   
127  [[bias, word.lower=galuh, word[-3:]=luh, word[...   
129  [[bias, word.lower=berlian, word[-3:]=ian, wor...   
132  [[bias, word.lower=kelurahan, word[-3:]=han, w...   
134  [[bias, word.lower=haji, word[-3:]=aji, word[-...   
135  [[bias, word.lower=gg, word[-3:]=gg, word[-2:]...   
136  [[bias, word.lower=jl, word[-3:]=jl, word[-2:]...   
137  [[bias, word.lower=sukun, word[-3:]=kun, word[...   
139  [[bias, word.lower=pancoran, word[-3:]=ran, wo...   
140  [[bias, word.lower=mt, word[-3:]=mt, word[-2:]...   
142  [[bias, word.lower=alamat, word[-3:]=mat, word...   
144  [[bias, word.lower=dr, word[-3:]=dr, word[-2:]...   
145  [[bias, word.lower=pt, word[-3:]=pt, word[-2:]...   
146  [[bias, word.lower=zahari, word[-3:]=ari, word...   
147  [[bias, word.lower=irda, word[-3:]=rda, word[-...   
153  [[bias, word.lower=makam, word[-3:]=kam, word[...   
154  [[bias, word.lower=universitas, word[-3:]=tas,...   
156  [[bias, word.lower=oke, word[-3:]=oke, word[-2...   
157  [[bias, word.lower=pes, word[-3:]=pes, word[-2...   
158  [[bias, word.lower=penyar, word[-3:]=yar, word...   
159  [[bias, word.lower=pak, word[-3:]=pak, word[-2...   
161  [[bias, word.lower=muti, word[-3:]=uti, word[-...   
163  [[bias, word.lower=kapuk, word[-3:]=puk, word[...   
165  [[bias, word.lower=budi, word[-3:]=udi, word[-...   
166  [[bias, word.lower=taman, word[-3:]=man, word[...   
168  [[bias, word.lower=pkbm, word[-3:]=kbm, word[-...   
169  [[bias, word.lower=warkop, word[-3:]=kop, word...   
170  [[bias, word.lower=yaya, word[-3:]=aya, word[-...   
172  [[bias, word.lower=sena, word[-3:]=ena, word[-...   
173  [[bias, word.lower=baksonya, word[-3:]=nya, wo...   
174  [[bias, word.lower=grand, word[-3:]=and, word[...   
175  [[bias, word.lower=bppv, word[-3:]=ppv, word[-...   
176  [[bias, word.lower=kragilan, word[-3:]=lan, wo...   
179  [[bias, word.lower=sela, word[-3:]=ela, word[-...   
182  [[bias, word.lower=sri, word[-3:]=sri, word[-2...   
187  [[bias, word.lower=bar, word[-3:]=bar, word[-2...   
189  [[bias, word.lower=jalan, word[-3:]=lan, word[...   
191  [[bias, word.lower=babakan, word[-3:]=kan, wor...   
192  [[bias, word.lower=sula, word[-3:]=ula, word[-...   
195  [[bias, word.lower=soji, word[-3:]=oji, word[-...   
198  [[bias, word.lower=kantor, word[-3:]=tor, word...   
199  [[bias, word.lower=deva, word[-3:]=eva, word[-...   
203  [[bias, word.lower=lela, word[-3:]=ela, word[-...   
205  [[bias, word.lower=dr., word[-3:]=dr., word[-2...   
207  [[bias, word.lower=kebon, word[-3:]=bon, word[...   
209  [[bias, word.lower=jl.tilung, word[-3:]=ung, w...   

                                                Y_test  \
119                   [POI, street, street, street, O]   
121         [O, street, street, street, O, O, O, O, O]   
123  [street, street, street, street, O, O, street,...   
125              [street, street, O, O, O, O, O, O, O]   
126                                 [O, O, O, O, O, O]   
127              [O, O, O, POI, POI, O, O, O, O, O, O]   
129                [POI, POI, O, street, street, O, O]   
132            [POI, POI, O, O, O, O, O, O, O, POI, O]   
134                              [O, O, O, O, O, O, O]   
135          [street, street, street, street, O, O, O]   
136   [O, O, O, O, O, O, O, O, O, O, O, O, O, O, O, O]   
137                                        [street, O]   
139                                         [POI, POI]   
140                                    [O, O, O, O, O]   
142          [O, POI, POI, O, O, O, O, O, O, POI, POI]   
144  [street, street, street, street, street, stree...   
145                       [POI, POI, POI, POI, POI, O]   
146                                          

In [105]:
print(bio_classification_report(y_test, y_pred))

              precision    recall  f1-score   support

           O       0.93      0.95      0.94    290663
         POI       0.84      0.83      0.83     89164
      street       0.91      0.88      0.89    142449

   micro avg       0.91      0.91      0.91    522276
   macro avg       0.89      0.89      0.89    522276
weighted avg       0.91      0.91      0.91    522276
 samples avg       0.91      0.91      0.91    522276



In [67]:
len(y_test)

107203

## Let's check what classifier learned

In [38]:
from collections import Counter
info = tagger.info()

def print_transitions(trans_features):
    for (label_from, label_to), weight in trans_features:
        print("%-6s -> %-7s %0.6f" % (label_from, label_to, weight))

print("Top likely transitions:")
print_transitions(Counter(info.transitions).most_common(15))

print("\nTop unlikely transitions:")
print_transitions(Counter(info.transitions).most_common()[-15:])

Top likely transitions:
POI    -> POI     2.782895
street -> street  1.596440
O      -> O       1.126601
POI    -> street  -0.464371
O      -> POI     -0.704975
street -> O       -0.832320
O      -> street  -0.885398
POI    -> O       -1.001872
street -> POI     -1.364160

Top unlikely transitions:
POI    -> POI     2.782895
street -> street  1.596440
O      -> O       1.126601
POI    -> street  -0.464371
O      -> POI     -0.704975
street -> O       -0.832320
O      -> street  -0.885398
POI    -> O       -1.001872
street -> POI     -1.364160


We can see that, for example, it is very likely that the beginning of an organization name (B-ORG) will be followed by a token inside organization name (I-ORG), but transitions to I-ORG from tokens with other labels are penalized. Also note I-PER -> B-LOC transition: a positive weight means that model thinks that a person name is often followed by a location.

Check the state features:

In [273]:
def print_state_features(state_features):
    for (attr, label), weight in state_features:
        print("%0.6f %-6s %s" % (weight, label, attr))    

print("Top positive:")
print_state_features(Counter(info.state_features).most_common(20))

print("\nTop negative:")
print_state_features(Counter(info.state_features).most_common()[-20:])

Top positive:
6.252076 street word.lower=sisin
6.019202 street word.lower=vete
6.008285 street word.lower=mongin
5.368430 street word.lower=sisingama
5.263754 O      word.lower=nomer
5.200193 O      -1:word.lower=sampurna
5.166381 street word.lower=let
5.048882 O      word.lower=karangsatria
4.873307 O      word.lower=busway
4.831546 O      word.lower=jatipulo
4.809483 O      word.lower=caturtunggal
4.798810 O      word.lower=masale
4.795045 POI    -1:word.lower=sh.
4.782880 O      word.lower=jaticempaka
4.732296 O      word.lower=batubulan
4.729333 O      word.lower=sidanegara
4.646149 street word.lower=komis
4.641072 street word.lower=cisa
4.597389 O      word.lower=jatikarya
4.528622 O      word.lower=jatimakmur

Top negative:
-3.232958 O      word.lower=tuba
-3.238960 O      word.lower=kan
-3.242788 street word.lower=cell
-3.246396 O      word.lower=mari
-3.285714 O      word.lower=lan
-3.332488 street +1:word.lower=jalan
-3.342390 street -1:word.lower=warkop
-3.376310 O      word.

In [171]:
big_list

[[5],
 [4],
 [1, 5],
 [4, 4],
 [4, 5],
 [4, 5],
 [1, 5],
 [4, 4, 5],
 [1, 4, 4],
 [1, 4, 5],
 [1, 4, 5],
 [1, 4, 4],
 [1, 4, 5],
 [1, 4, 5],
 [1, 4, 4, 5],
 [1, 4, 4, 5],
 [1, 1, 4, 4, 5],
 [1, 1, 4, 4, 5]]

In [256]:
def combinations(lst, n,taste_val): 
      
    if n == 0: 
        return [[]] 
      
    l =[]
#     if ((sum(number_list)/len(number_list))/taste_val) >= 1:
    for i in range(0, len(lst)): 
        m = lst[i]
        remLst = lst[i + 1:] 

        for p in combinations(remLst, n-1,taste_val):
            combined_list = [m] +p
            combined_list = [int(x) for x in combined_list]

            if ((sum(combined_list)/len(combined_list))/taste_val) >= 1:
                l.append(combined_list)
            else:
                pass

    return l

L = [1,1,4,5,1,4]

first_line = '6 3'
second_line = '1 1 4 5 1 4'
second_line = second_line.split(' ')
length_n = int(first_line.split(' ')[0])
taste_value = int(first_line.split(' ')[1])
big_list = []
compiled_list = []
# bigger_list = 
for i in range(1,len(second_line)+1):
    list_item = list(set([",".join(map(str, comb)) for comb in combinations(second_line, i,taste_value)]))
    if len(list_item):
        for each_combi in list_item:
            print(number_list)
            number_list = each_combi.split(',')
            number_list = [int(x) for x in number_list ]
            compiled_list.append(number_list)

sort_big_list = [sorted(each_item) for each_item in compiled_list ]
sorted_big_list = sorted(sort_big_list)
count = 0
morethan_count = 0
for ind,item in enumerate(sorted_big_list):
    if ((sum(item)/len(item))/3) >= 1:
        morethan_count = morethan_count + 1
        if ind+1 < len(sorted_big_list):
            if sorted_big_list[ind+1] == item:
                count = count + 1
            
final = morethan_count - count
print(final)

['']
[5]
[4]
[1, 5]
[5, 4]
[4, 5]
[4, 4]
[1, 4, 4]
[4, 5, 4]
[1, 4, 5]
[1, 5, 4]
[1, 4, 5, 4]
10


In [263]:
import numpy as np

def cartesian(arrays, out=None):
    """
    Generate a cartesian product of input arrays.

    Parameters
    ----------
    arrays : list of array-like
        1-D arrays to form the cartesian product of.
    out : ndarray
        Array to place the cartesian product in.

    Returns
    -------
    out : ndarray
        2-D array of shape (M, len(arrays)) containing cartesian products
        formed of input arrays.

    Examples
    --------
    >>> cartesian(([1, 2, 3], [4, 5], [6, 7]))
    array([[1, 4, 6],
           [1, 4, 7],
           [1, 5, 6],
           [1, 5, 7],
           [2, 4, 6],
           [2, 4, 7],
           [2, 5, 6],
           [2, 5, 7],
           [3, 4, 6],
           [3, 4, 7],
           [3, 5, 6],
           [3, 5, 7]])

    """

    arrays = [np.asarray(x) for x in arrays]
    dtype = arrays[0].dtype

    n = np.prod([x.size for x in arrays])
    if out is None:
        out = np.zeros([n, len(arrays)], dtype=dtype)

    m = n / arrays[0].size
    out[:,0] = np.repeat(arrays[0], m)
    if arrays[1:]:
        cartesian(arrays[1:], out=out[0:m, 1:])
        for j in xrange(1, arrays[0].size):
            out[j*m:(j+1)*m, 1:] = out[0:m, 1:]
    return out
L = [[1,3,2],[1],[4],[5],[1],[4]]

cartesian(([1, 2, 3], [4, 5], [6, 7]))

TypeError: slice indices must be integers or None or have an __index__ method

[[1],
 [1, 1],
 [1, 1, 1],
 [1, 1, 1, 4],
 [1, 1, 4],
 [1, 1, 4, 1],
 [1, 1, 4, 1, 4],
 [1, 1, 4, 4],
 [1, 1, 4, 5],
 [1, 1, 4, 5, 1],
 [1, 1, 4, 5, 1, 4],
 [1, 1, 4, 5, 4],
 [1, 1, 5],
 [1, 1, 5, 1],
 [1, 1, 5, 1, 4],
 [1, 1, 5, 4],
 [1, 4],
 [1, 4, 1],
 [1, 4, 1, 4],
 [1, 4, 4],
 [1, 4, 5],
 [1, 4, 5, 1],
 [1, 4, 5, 1, 4],
 [1, 4, 5, 4],
 [1, 5],
 [1, 5, 1],
 [1, 5, 1, 4],
 [1, 5, 4],
 [4],
 [4, 1],
 [4, 1, 4],
 [4, 4],
 [4, 5],
 [4, 5, 1],
 [4, 5, 1, 4],
 [4, 5, 4],
 [5],
 [5, 1],
 [5, 1, 4],
 [5, 4]]

In [235]:
sorted_big_list

[[1],
 [1, 1],
 [1, 1, 1],
 [1, 1, 1, 4],
 [1, 1, 1, 4],
 [1, 1, 1, 4, 4],
 [1, 1, 1, 4, 4, 5],
 [1, 1, 1, 4, 5],
 [1, 1, 1, 4, 5],
 [1, 1, 1, 5],
 [1, 1, 4],
 [1, 1, 4],
 [1, 1, 4, 4],
 [1, 1, 4, 4],
 [1, 1, 4, 4, 5],
 [1, 1, 4, 4, 5],
 [1, 1, 4, 5],
 [1, 1, 4, 5],
 [1, 1, 4, 5],
 [1, 1, 4, 5],
 [1, 1, 5],
 [1, 1, 5],
 [1, 4],
 [1, 4],
 [1, 4, 4],
 [1, 4, 4],
 [1, 4, 4, 5],
 [1, 4, 4, 5],
 [1, 4, 5],
 [1, 4, 5],
 [1, 4, 5],
 [1, 4, 5],
 [1, 5],
 [1, 5],
 [4],
 [4, 4],
 [4, 4, 5],
 [4, 5],
 [4, 5],
 [5]]

In [238]:
len(sorted_big_list)

40

In [239]:
sort_big_list = [sorted(each_item) for each_item in compiled_list ]
sorted_big_list = sorted(sort_big_list)
count = 0
morethan_count = 0
for ind,item in enumerate(sorted_big_list):
    if ((sum(item)/len(item))/3) >= 1:
        morethan_count = morethan_count + 1
        if ind+1 < len(sorted_big_list):
            if sorted_big_list[ind+1] == item:
                print(sorted_big_list[ind+1])
                print(item)
                count = count + 1
                print(count)
            
final = morethan_count - count
print(final)

[1, 1, 4, 4, 5]
[1, 1, 4, 4, 5]
1
[1, 4, 4]
[1, 4, 4]
2
[1, 4, 4, 5]
[1, 4, 4, 5]
3
[1, 4, 5]
[1, 4, 5]
4
[1, 4, 5]
[1, 4, 5]
5
[1, 4, 5]
[1, 4, 5]
6
[1, 5]
[1, 5]
7
[4, 5]
[4, 5]
8
10


In [233]:
count

17

In [234]:
morethan_count

18

In [180]:
import itertools
print(big_list)
len(list(num for num,_ in itertools.groupby(sorted(big_list))))

[[5], [4], [1, 5], [4, 4], [4, 5], [4, 5], [1, 5], [4, 4, 5], [1, 4, 4], [1, 4, 5], [1, 4, 5], [1, 4, 4], [1, 4, 5], [1, 4, 5], [1, 4, 4, 5], [1, 4, 4, 5], [1, 1, 4, 4, 5], [1, 1, 4, 4, 5]]


10